In [1]:
import astropy
import astropy.units as u

from astroquery.sdss import SDSS

import numpy as np

import pandas as pd

from astropixie.data import SDSSRegion
import astropixie_widgets  as aww

aww.config.setup_notebook(debug=False)

/Users/jmatt/.local/share/virtualenvs/investigations-Jw_U-l6l/lib/python3.6/site-packages/astroquery/sdss/__init__.py:29: UserWarning: Experimental: SDSS has not yet been refactored to have its API match the rest of astroquery (but it's nearly there).
  warnings.warn("Experimental: SDSS has not yet been refactored to have its API "


In [71]:
coord_strs_source = '''
0001	383	5 32 28.192	00 11 30.26
0003	383	5 32 37.882	00 09 42.00
0006	383	5 32 28.229	00 12 58.45
0011	383	5 32 36.763	00 11 04.83
0016	383	5 32 30.995	00 13 38.83
0018	383	5 32 29.692	00 12 25.97
0025	383	5 32 38.997	00 09 27.24
0029	383	5 32 42.341	00 12 28.39
0041	383	5 32 41.368	00 09 25.18
0045	383	5 32 29.721	00 08 53.50
0058	383	5 32 38.405	00 12 36.67
0080	383	5 32 28.521	00 10 47.58
0084	383	5 32 44.212	00 10 37.32
0090	383	5 32 46.460	00 12 34.97
0093	383	5 32 35.225	00 08 51.66
0117	383	5 32 46.802	00 11 19.68
0165	383	5 32 38.759	00 13 42.46
'''


def coords_source():
    coords_source = []
    for line in coord_strs_source.split('\n'):
        if line:
            parsed = line.split('\t')
            ra = parsed[-2].replace(' ', ':')
            dec = parsed[-1].replace(' ', ':')
            coords_source.append((int(parsed[0]), '{0} {1}'.format(ra, dec)))
    return coords_source


query = """
SELECT TOP 3200
        p.objID,
        p.ra,
        p.dec,
        p.psfMag_u,
        p.psfMag_g,
        p.psfMag_r,
        p.psfMag_i,
        p.psfMag_z,
        (p.psfMag_u - p.extinction_u) AS u,
        (p.psfMag_g - p.extinction_g) AS g,
        (p.psfMag_r - p.extinction_r) AS r,
        (p.psfMag_i - p.extinction_i) AS i,
        (p.psfMag_z - p.extinction_z) AS z,
        (p.psfMag_u - p.extinction_u) AS u_corrected,
        (p.psfMag_g - p.extinction_g) AS g_corrected,
        (p.psfMag_r - p.extinction_r) AS r_corrected,
        (p.psfMag_i - p.extinction_i) AS i_corrected,
        (p.psfMag_z - p.extinction_z) AS z_corrected,
        p.psfMagErr_u,
        p.psfMagErr_g,
        p.psfMagErr_r,
        p.psfMagErr_i,
        p.psfMagErr_z,
        p.flags,
        p.skyVersion,
        p.raErr,
        p.decErr,
        p.extinction_u,
        p.extinction_g,
        p.extinction_r,
        p.extinction_i,
        p.extinction_z,
        p.modelMag_u,
        p.modelMag_g,
        p.modelMag_r,
        p.modelMag_i,
        p.modelMag_z,
        p.dered_u,
        p.dered_g,
        p.dered_r,
        p.dered_i,
        p.dered_z,
        p.specObjID,
        p.score
FROM PhotoPrimary AS p
JOIN dbo.fGetNearbyObjEq(83.15416667, 0.18833333, 7.24)
  AS r ON r.objID = p.objID
WHERE p.probPSF = 1
"""

region = SDSSRegion()


def create_coords(cat):
    coords = []
    for row in region.cat:
        coords.append((row['objID'],
                       astropy.coordinates.SkyCoord(
                           ra=row['ra']*u.degree, 
                           dec=row['dec']*u.degree,
                           frame='icrs')))
    return coords


coords = create_coords(region.cat)


def is_match(c1, c2, atol=1.e-4):
    if np.isclose([c1.ra.degree], [c2.ra.degree], rtol=1.e-4, atol=atol)[0] \
        and np.isclose([c1.dec.degree], [c2.dec.degree], rtol=1.e-4, atol=atol)[0]:
            return True

        
def match_coord(coord_str):
    """Return a list of tuples with the SDSS objID and row for objects close to the coord_str location."""
    coord = astropy.coordinates.SkyCoord(coord_str, unit=(u.hourangle, u.deg), frame='icrs')
    matches = []
    for id_, c in coords:
        match = is_match(coord, c)
        #if not match:
        #    match = find_match(coord, c, atol=1.e-3)
        if match:
            matches.append(id_)
    matches_row = []
    for row in region.cat:
        if row['objID'] in matches:
            matches_row.append(row)
    return matches_row

def match_coords():
    rows = []
    for webda_id, c in coords_source():
        rows.append((webda_id, match_coord(c)))
    return rows

mcs = match_coords()
mcs

[(1, [<Row index=0>
          objID               ra               dec           u        g        r        i       z     psfMag_u psfMag_g psfMag_r psfMag_i psfMag_z psfMagErr_u psfMagErr_g psfMagErr_r psfMagErr_i psfMagErr_z      flags      skyVersion       raErr              decErr       extinction_u extinction_g extinction_r extinction_i extinction_z modelMag_u modelMag_g modelMag_r modelMag_i modelMag_z dered_u  dered_g dered_r  dered_i  dered_z  specObjID   score  
          int64            float64           float64      float64  float64  float64  float64 float64  float64  float64  float64  float64  float64    float64     float64     float64     float64     float64        int64        int64         float64            float64         float64      float64      float64      float64      float64     float64    float64    float64    float64    float64   float64  float64 float64  float64  float64    int64    float64 
   ------------------- ---------------- ----------------- -------- -

In [1]:
macminn_dat_str = ''' 0001    577.2     68.7     13.331      0.580
 0002    188.4     64.2     13.596      0.718
 0003    223.9    546.3     13.682      1.034
 0004    580.1    622.4     14.318      0.730
 0005    511.4    549.2     14.798      1.488
 0006    866.5     68.6     14.929      0.861
 0007    567.5    450.1     15.024      0.968
 0008    546.9    598.4     15.154      1.427
 0009    488.8    166.4     15.316      0.870
 0010    385.0    612.3     15.756      1.213
 0011    495.5    490.8     16.177      1.248
 0012    292.5    727.9     16.209      1.278
 0013    791.9    404.3     16.226      0.627
 0014    292.5    727.9     16.243     -0.669
 0015    543.3    505.6     16.362      1.120
 0016    999.5    204.3     16.525      0.888
 0017    548.4    406.6     16.531      0.874
 0018    760.4    141.2     16.571      0.838
 0019    413.4    346.3     16.707      0.741
 0020    510.5    465.6     16.871      0.458
 0021    478.5    510.7     16.891      0.752
 0022    642.1    495.8     16.904      1.181
 0023    526.4    466.7     16.908      0.284
 0024    529.1    519.9     16.954      0.535
 0025    175.7    602.1     16.959      0.802
 0026    202.3     91.5     17.036      1.318
 0027    198.9    316.7     17.073      1.197
 0028    536.0    557.7     17.111      1.158
 0029    774.4    763.1     17.140      1.129
 0030    534.4    269.2     17.199      1.147
 0031    470.8    406.0     17.351      1.135
 0032    449.5    249.8     17.398      0.600
 0033    678.4    501.9     17.433      1.151
 0034    614.0    435.8     17.469      1.136
 0035    790.6    334.5     17.487      0.817
 0036    414.1    375.7     17.496      0.378
 0037    456.8    318.5     17.511      1.126
 0038    263.6    497.1     17.561      1.025
 0039    601.9    329.4     17.606      1.135
 0040    544.2    444.6     17.622      0.594
 0041    169.4    718.9     17.632      1.398
 0042    564.3    471.5     17.679      1.126
 0043    579.7    383.4     17.679      0.417
 0044    540.6    556.0     17.692      0.796
 0045     63.1    145.5     17.692      1.278
 0046    857.5     11.7     17.767      0.966
 0047    396.5    441.0     17.849      0.367
 0048     99.3    557.2     17.869      0.774
 0049    517.3    535.2     17.910      0.815
 0050    446.7    407.8     17.952      0.737
 0051    328.2    841.7     17.973      2.013
 0052     28.7    976.3     17.981      1.324
 0053    254.0    538.9     18.023      0.596
 0054    500.0    295.0     18.073      0.745
 0055    262.8    228.6     18.103      0.825
 0056    513.4    605.8     18.105      0.785
 0057    400.0    420.3     18.110      0.784
 0058    797.3    569.6     18.123      0.800
 0059    297.3    336.7     18.124      0.895
 0060    540.8    514.1     18.127      0.846
 0061    629.5    429.3     18.148      0.837
 0062    482.6    489.7     18.154      0.796
 0063    538.9    538.1     18.167      0.814
 0064    521.7    470.6     18.178      0.729
 0065    403.4    271.6     18.200      0.769
 0066    678.4    209.1     18.207      1.106
 0067    577.9    429.2     18.209      0.935
 0068    349.4    107.5     18.228      1.036
 0069    402.9    209.3     18.236      0.738
 0070     82.1    546.3     18.240      0.761
 0071    625.4    425.4     18.241      0.796
 0072    820.6    142.8     18.246      0.961
 0073    615.1    647.3     18.252      0.841
 0074    537.8    605.2     18.260      0.860
 0075    580.9    864.5     18.264      0.957
 0076    656.3    517.6     18.266      0.783
 0077    623.9    391.4     18.270      0.798
 0078    389.3    436.2     18.278      0.746
 0079    624.7    646.8     18.286      0.829
 0080    436.9     84.9     18.292      0.968
 0081    396.2    256.8     18.303      0.764
 0082    303.2    618.4     18.311      0.821
 0083    584.9    474.6     18.319      0.883
 0084    407.1    857.0     18.323      1.282
 0085    393.5    658.7     18.341      0.772
 0086    529.4    377.1     18.363      0.733
 0087    761.0    359.0     18.366      0.802
 0088    598.9    573.5     18.405      0.679
 0089    778.5    524.0     18.407      0.781
 0090    793.8    967.2     18.425      1.127
 0091    510.7    541.7     18.431      0.986
 0092    579.5    569.5     18.437      0.753
 0093     58.4    416.3     18.437      0.775
 0094    676.0    297.9     18.453      0.760
 0095    456.8    603.3     18.472      0.754
 0096    658.9    500.0     18.494      0.799
 0097    462.3    630.3     18.500      0.772
 0098    749.7    636.3     18.509      0.795
 0099    602.7    753.1     18.528      1.186
 0100    253.5    651.1     18.532      2.179
 0101     30.9    237.2     18.565      1.27
 0102    574.0    259.5     18.580      0.738
 0103      8.9    854.0     18.595      0.802
 0104    423.9    391.6     18.596      0.729
 0105    518.5    485.0     18.597      0.727
 0106    531.2    714.8     18.611      0.880
 0107    354.9    144.8     18.621      0.766
 0108    516.5    447.5     18.659      0.722
 0109    560.5    150.0     18.673      0.877
 0110    679.3    542.9     18.683      0.755
 0111    668.3    414.7     18.687      0.734
 0112     93.9    412.1     18.697      1.352
 0113    370.6    383.1     18.704      0.706
 0114    548.2    884.9     18.708      1.045
 0115    718.0    265.9     18.729      0.761
 0116    643.3    389.7     18.751      2.235
 0117    546.5    985.2     18.758      2.685
 0118    533.7    498.7     18.773      0.801
 0119    275.3    387.0     18.785      0.770
 0120    669.9    551.9     18.789      0.760
 0121    684.7    340.6     18.810      0.684
 0122    587.8    293.7     18.811      0.726
 0123    441.8    489.0     18.814      0.736
 0124    330.3    817.2     18.832      1.061
 0125    399.7    450.0     18.838      0.744
 0126    777.5    191.8     18.841      0.767
 0127    213.4    567.0     18.843      0.801
 0128    323.0    514.5     18.849      0.758
 0129    487.6    566.1     18.853      0.482
 0130    474.8    541.9     18.856      0.996
 0131    269.8    567.2     18.859      0.765
 0132    563.5    479.5     18.864      0.710
 0133    571.6    522.5     18.868      0.797
 0134    441.2    340.4     18.894      0.756
 0135    570.3    575.4     18.900      0.785
 0136    523.5    475.6     18.916      0.838
 0137    358.3    381.6     18.923      0.791
 0138    244.2     28.0     18.929      0.881
 0139    416.9    658.9     18.939      0.768
 0140    509.2    475.1     18.943      0.772
 0141    125.6    476.7     18.947      0.823
 0142    672.3    844.9     18.947      1.205
 0143    608.4    331.3     18.965      0.903
 0144    957.7    542.2     18.969      1.163
 0145    247.7    711.5     18.997      1.827
 0146    611.3    544.2     19.015      0.877
 0147    473.9    440.4     19.034      0.745
 0148    340.3    476.2     19.036      0.785
 0149    589.9    145.0     19.046      1.217
 0150    394.0    933.2     19.052      0.876
 0151    932.3    105.5     19.055      1.587
 0152    389.6    493.8     19.068      0.743
 0153     62.6    322.3     19.078      0.726
 0154    224.9    979.8     19.085      1.310
 0155     29.1    973.3     19.085     -0.772
 0156    168.8    410.9     19.109      0.832
 0157    488.7    464.1     19.114      0.801
 0158    523.0    483.1     19.123      0.806
 0159    761.2    493.8     19.124      1.113
 0160    808.3    434.6     19.129      0.926
 0161    207.8     72.2     19.133      3.231
 0162    787.3    330.8     19.138      0.763
 0163    296.1    181.8     19.168      0.838
 0164    788.5    125.7     19.171      1.938
 0165   1013.4    586.93    19.186      1.442
 0166    660.8    491.519   19.191      0.792
 0167    472.1    540.965   19.210      0.422
 0168    628.9    434.197   19.212      1.048
 0169    505.7    496.455   19.220      0.803
 0170    676.6    362.076   19.242      0.820
 0171    679.2    215.839   19.265      0.751
 0172    465.7    248.155   19.280      0.769
 0173    749.2    365.309   19.289      0.805
 0174    463.3    471.362   19.307      0.763
 0175    422.9    634.475   19.308      1.068
 0176    816.3    203.371   19.311      0.827
 0177    408.7    275.421   19.317      0.800
 0178    568.7    288.991   19.327      0.757
 0179    776.3    738.568   19.327      1.601
 0180    603.5    606.161   19.336      0.940
 0181    377.2    1010.14   19.338      2.466
 0182    510.8    397.755   19.339      0.832
 0183    521.6    748.791   19.342      1.057
 0184    490.5    564.065   19.348      0.794
 0185    812.3    756.309   19.359      0.834
 0186    454.017  378.646   19.361      0.774
 0187    509.978  491.109   19.367      0.809
 0188    566.808  492.675   19.406      0.833
 0189    725.587  431.861   19.423      0.861
 0190    836.775  795.983   19.424      1.783
 0191    702.863  313.839   19.441      0.790
 0192    391.491  564.507   19.460      0.803
 0193    236.851  700.948   19.465      0.899
 0194    945.117  297.258   19.491      0.844
 0195    868.295  268.568   19.495      0.898
 0196    471.438  627.751   19.505      0.799
 0197    100.801  124.834   19.507      1.016
 0198    980.362  639.356   19.518      1.408
 0199    629.316  834.558   19.518      1.183
 0200    632.844  516.271   19.552      0.827
 0201    289.649  783.135   19.554      0.863
 0202    614.976  801.15    19.557      0.841
 0203    350.069  261.878   19.565      0.786
 0204    547.975  445.649   19.571      0.801
 0205    608.492  417.19    19.574      0.868
 0206    907.931  924.381   19.607      1.178
 0207     662.68  353.712   19.620      0.875
 0208    605.845  479.598   19.621      0.806
 0209    162.848  371.422   19.621      1.164
 0210    453.005  340.839   19.622      0.842
 0211    795.591  391.393   19.631      1.662
 0212    714.398   97.052   19.631      0.982
 0213    356.317  992.699   19.638      0.511
 0214     39.666  730.617   19.647      0.899
 0215    336.627  520.173   19.669      0.890
 0216    307.929  838.373   19.674      0.994
 0217    214.262  816.425   19.685      1.927
 0218     650.21  899.237   19.699      0.871
 0219     41.008  619.532   19.711      1.211
 0220    303.364  535.074   19.721      0.804
 0221     884.03  599.149   19.739      0.915
 0222    633.461  962.639   19.753      1.277
 0223    270.183  728.866   19.766      0.839
 0224    190.004  839.339   19.770      0.888
 0225    850.603  305.777   19.771      0.867
 0226    609.818  294.833   19.774      0.904
 0227    119.696  344.659   19.774      0.799
 0228    474.717  457.608   19.791      0.843
 0229    681.133  803.976   19.794      0.944
 0230    671.496  284.415   19.796      1.892
 0231    768.937  486.074   19.800      1.326
 0232    671.496  284.415   19.801      1.611
 0233    683.689  103.414   19.802      0.886
 0234    629.133  444.234   19.829      0.823
 0235    840.806  980.633   19.831      1.093
 0236    429.337  472.887   19.831      0.827
 0237    363.062  428.678   19.835      0.807
 0238    890.703  473.568   19.837      0.927
 0239    730.862  279.342   19.842      2.448
 0240    503.644  569.002   19.873      0.845
 0241    531.645  451.352   19.874      0.953
 0242    372.679  764.366   19.875      0.868
 0243    144.156  934.352   19.880      0.898
 0244    280.704  648.553   19.884      0.881
 0245    326.026  657.86    19.898      0.953
 0246    650.996  300.297   19.908      0.895
 0247    793.088  485.996   19.908      1.064
 0248     526.12  458.184   19.914      0.971
 0249    244.826  645.354   19.935      0.942
 0250    830.884  371.494   19.938      0.868
 0251    839.706  338.621   19.938      0.883
 0252    665.842  254.807   19.964      0.841
 0253    751.054  610.88    19.966      0.956
 0254    306.975  317.116   19.973      0.832
 0255    655.969  432.906   19.974      0.794
 0256    420.318  604.627   19.986      2.211
 0257    369.584  602.954   19.989      0.971
 0258    485.668  660.422   19.991      0.845
 0259    909.801  740.719   20.015      1.689
 0260    899.657  575.7     20.023      0.867
 0261    225.082  977.079   20.027      0.528
 0262    438.605  395.275   20.032      0.783
 0263    914.029  739.145   20.034      0.365
 0264    291.726  575.844   20.038      0.888
 0265    914.029  739.145   20.040     -0.005
 0266     688.52  489.719   20.043      0.901
 0267    710.588  616.605   20.044      0.859
 0268    273.446  971.03    20.051      1.043
 0269    644.668  279.335   20.054      2.617
 0270    800.879  994.51    20.055      1.076
 0271    501.697  185.805   20.057      0.864
 0272     21.575  957.909   20.060      1.038
 0273    753.167   53.87    20.061      1.022
 0274    418.422  476.94    20.088      0.825
 0275    416.765  935.674   20.116      0.925
 0276    356.274  688.929   20.123      0.970
 0277    595.754  483.865   20.130      0.853
 0278    669.372  333.478   20.143      0.893
 0279     572.36   29.86    20.148      0.846
 0280    243.789  757.15    20.155      0.949
 0281    559.539  668.768   20.158      0.917
 0282    543.348  751.539   20.175      0.930
 0283    907.535  368.369   20.177      0.907
 0284    644.207  618.528   20.191      0.830
 0285    517.884  765.026   20.194      0.927
 0286    334.516  781.07    20.206      1.069
 0287    950.294   78.806   20.215      0.939
 0288      62.19  763.442   20.215      1.293
 0289    507.246  341.738   20.217      0.853
 0290    539.832  394.912   20.226      0.982
 0291     980.99  534.348   20.257      1.632
 0292       558.  537.109   20.274      0.985
 0293    678.679  704.699   20.276      0.912
 0294    271.654  285.077   20.299      0.894
 0295    995.228  735.899   20.303      0.977
 0296     473.48  570.896   20.308      0.862
 0297    444.824  496.429   20.312      0.890
 0298     25.522  485.876   20.319      0.840
 0299    459.198  457.356   20.324      0.855
 0300    729.872  443.808   20.337      0.926
 0301    317.029  529.489   20.357      0.954
 0302    559.055  313.351   20.373      1.019
 0303    241.791  616.679   20.374      0.953
 0304    633.679  533.742   20.422      0.929
 0305    386.204  652.065   20.425      0.950
 0306    1008.77  626.34    20.464      0.965
 0307    576.135  579.398   20.485      0.928
 0308    715.605  571.991   20.488      0.946
 0309    669.755  100.552   20.495      1.792
 0310    520.592  422.116   20.519      0.994
 0311    709.011  156.416   20.539      0.947
 0312    892.723  850.874   20.549      1.080
 0313    471.467   55.817   20.568      0.914
 0314    126.637  979.961   20.578      2.088
 0315    164.082  742.485   20.584      1.102
 0316    553.044  1015.01   20.594      1.001
 0317    343.101  114.154   20.599      2.788
 0318    837.804  175.775   20.599      1.159
 0319    511.085  380.282   20.617      1.068
 0320    518.278  456.289   20.707      1.014
 0321    657.941  354.791   20.724      0.954
 0322     61.681  247.995   20.728      2.263
 0323    563.237  518.146   20.732      0.926
 0324    306.519  730.848   20.739      1.227
 0325    120.741  181.482   20.754      1.350
 0326    557.871  491.038   20.759      1.025
 0327    617.932  704.527   20.760      1.156
 0328    378.456  414.731   20.772      1.002
 0329    356.539  995.089   20.800      1.455
 0330    659.086  431.414   20.807      1.058
 0331    826.517  541.985   20.842      1.071
 0332    576.207  754.766   20.847      0.996
 0333    739.863  809.372   20.850      1.859
 0334    860.892  956.711   20.854      2.237
 0335    589.649  590.732   20.875      1.164
 0336    455.887  616.781   20.910      1.111
 0337    998.799  522.662   20.916      1.212
 0338    844.171  367.729   20.925      1.037
 0339    156.204  276.807   20.941      1.793
 0340    686.153  164.643   20.955      1.018
 0341    899.338  927.256   20.961      1.061
 0342    540.396  157.251   20.964      1.183
 0343    435.201  568.924   20.965      1.241
 0344    390.051  416.594   20.966      2.135
 0345    705.455  418.541   20.967      0.994
 0346    1017.05  124.43    20.971      1.024
 0347    420.313  253.844   20.979      0.977
 0348    870.386    7.173   20.984      1.402
 0349     24.954  233.159   20.999      1.085
 0350    719.895  608.573   21.021      0.960
 0351    328.048  769.524   21.021      1.966
 0352     397.95  595.733   21.045      1.043
 0353    435.814  397.808   21.048      1.188
 0354    731.578   39.485   21.059      1.047
 0355    486.112  209.85    21.066      1.142
 0356    422.244  761.847   21.073      1.100
 0357    854.379  261.7     21.088      2.478
 0358    424.334  452.648   21.093      1.014
 0359     64.723  615.221   21.096      1.118
 0360    1004.47  604.993   21.103      1.127
 0361    639.979  162.54    21.122      1.042
 0362    552.325  528.605   21.122      1.221
 0363    288.015  603.776   21.143      1.014
 0364    171.078  535.451   21.219      1.110
 0365    230.552  112.869   21.221      0.818
 0366    982.319  469.005   21.221      2.722
 0367    123.103  875.365   21.228      3.000
 0368     94.178  424.645   21.235      0.913
 0369    657.365  684.162   21.237      1.174
 0370    420.347  357.33    21.255      1.100
 0371    535.282  320.686   21.255      1.050
 0372     519.96  518.542   21.276      1.162
 0373     99.567  871.698   21.287      0.689
 0374    862.493  379.628   21.303      2.118
 0375    651.431  319.274   21.307      1.039
 0376     737.89  629.573   21.330      0.797
 0377     522.4   498.5     21.334      2.352
 0378    983.728  198.466   21.340      1.383
 0379    236.058  596.454   21.380      1.099
 0380     657.91  382.606   21.383      2.973
 0381    506.674  466.813   21.429      1.320
 0382     79.941  288.094   21.446      1.124
 0383    982.933  476.318   21.455      1.261
 0384     98.218   78.499   21.472      1.199
 0385    192.102  625.981   21.505      1.264
 0386    300.658  303.891   21.508      1.163
 0387    715.741  210.975   21.509      1.171
 0388    936.084  341.707   21.520      1.903
 0389    718.121  382.404   21.521      2.410
 0390    525.207  354.194   21.531      1.153
 0391    166.503  772.303   21.542      1.138
 0392    602.201  280.156   21.544      0.911
 0393    154.234   78.065   21.555      1.137
 0394    523.556  339.173   21.559      1.038
 0395    916.621  530.065   21.561      1.193
 0396    413.349  327.311   21.572      1.260
 0397    537.437  476.869   21.584      1.026
 0398    983.233  491.748   21.588      1.188
 0399    602.476  502.392   21.591      0.959
 0400    173.542 1010.92    21.620      2.482
 0401    276.055 1017.37    21.631      1.067
 0402     438.96  165.558   21.647      1.136
 0403    315.614  407.014   21.661      1.787
 0404      515.6  439.024   21.663      1.030
 0405    461.975  334.568   21.666      1.202
 0406    438.218  378.75    21.691      2.580
 0407    673.955  166.541   21.693      1.646
 0408     215.06  398.492   21.724      1.307
 0409    741.809  354.151   21.732      1.238
 0410     71.799  754.333   21.784      1.120
 0411      491.6  352.62    21.785      1.136
 0412    904.196  775.724   21.813      1.233
 0413     11.656  835.098   21.814      1.292
 0414    448.985  562.515   21.820      1.487
 0415    419.585  608.453   21.823      1.212
 0416    908.682  276.158   21.863      3.017
 0417    549.456  173.26    21.865      1.771
 0418    455.487  898.283   21.884      1.302
 0419    263.443  508.431   21.886      1.252
 0420    550.949  491.556   21.888      1.168
 0421     79.835  389.321   21.904      1.218
 0422    456.685  678.179   21.952      2.777
 0423    566.941  393.581   21.954      1.256
 0424    922.832  801.582   21.983      2.107
 0425    854.636  970.685   21.985      2.091
 0426     641.29  135.045   21.994      1.280
 0427    419.738   43.138   22.095      1.376
 0428    950.933   26.661   22.150      3.438
 0429    193.064  919.366   22.157      2.217
'''


macminn_dat = [l.split() for l in macminn_dat_str.split('\n') if l]
macminn_dat = [{'webda': int(l[0]), 'x': float(l[1]), 'y': float(l[2]), 'V': float(l[3]), 'VI': float(l[4])} for l in macminn_dat]


mcs_ones = []


for m in mcs:
    if m[1]:
        mcs_ones.append((m[0], m[1][0]))
mcs_ones

cross = []
for id_, sdss_row in mcs_ones:
    macminn_ = macminn_dat[id_ - 1]
    for c in sdss_row.columns:
        macminn_[c] = sdss_row[c]
    cross.append(macminn_)

cross

NameError: name 'mcs' is not defined

In [73]:
webda_xy_str = """
0001	13.33	-422.10	81.7
0002	13.60	-426.60	-307.1
0003	13.68	55.50	-271.6
0004	14.32	131.60	84.6
0005	14.80	58.40	15.9
0006	14.93	-422.20	371
0007	15.02	-40.70	72
0008	15.15	107.60	51.4
0009	15.32	-324.40	-6.7
0010	15.76	121.50	-110.5
0011	16.18	0.00	0
0012	16.21	237.10	-203
0013	16.23	-86.50	296.4
0014	16.24	237.10	-203
0015	16.36	14.80	47.8
0016	16.52	-286.50	504
0017	16.53	-84.20	52.9
0018	16.57	-349.60	264.9
0019	16.71	-144.50	-82.1
0020	16.87	-25.20	15
0021	16.89	19.90	-17
0022	16.90	5.00	146.6
0023	16.91	-24.10	30.9
0024	16.95	29.10	33.6
0025	16.96	111.30	-319.8
0026	17.04	-399.30	-293.2
0027	17.07	-174.10	-296.6
0028	17.11	66.90	40.5
0029	17.14	272.30	278.9
0030	17.20	-221.60	38.9
0031	17.35	-84.80	-24.7
0032	17.40	-241.00	-46
0033	17.43	11.10	182.9
0034	17.47	-55.00	118.5
0035	17.49	-156.30	295.1
0036	17.50	-115.10	-81.4
0037	17.51	-172.30	-38.7
0038	17.56	6.30	-231.9
0039	17.61	-161.40	106.4
0040	17.62	-46.20	48.7
0041	17.63	228.10	-326.1
0042	17.68	-19.30	68.8
0043	17.68	-107.40	84.2
0044	17.69	65.20	45.1
0045	17.69	-345.30	-432.4
0046	17.77	-479.10	362
0047	17.85	-49.80	-99
0048	17.87	66.40	-396.2
0049	17.91	44.40	21.8
0050	17.95	-83.00	-48.8
0051	17.97	350.90	-167.3
0052	17.98	485.50	-466.8
0053	18.02	48.10	-241.5
0054	18.07	-195.80	4.5
0055	18.10	-262.20	-232.7
0056	18.11	115.00	17.9
0057	18.11	-70.50	-95.5
0058	18.12	78.80	301.8
0059	18.12	-154.10	-198.2
0060	18.13	23.30	45.3
0061	18.15	-61.50	134
0062	18.15	-1.10	-12.9
0063	18.17	47.30	43.4
0064	18.18	-20.20	26.2
0065	18.20	-219.20	-92.1
0066	18.21	-281.70	182.9
0067	18.21	-61.60	82.4
0068	18.23	-383.30	-146.1
0069	18.24	-281.50	-92.6
0070	18.24	55.50	-413.4
0071	18.24	-65.40	129.9
0072	18.25	-348.00	325.1
0073	18.25	156.50	119.6
0074	18.26	114.40	42.3
0075	18.26	373.70	85.4
0076	18.27	26.80	160.8
0077	18.27	-99.40	128.4
0078	18.28	-54.60	-106.2
0079	18.29	156.00	129.2
0080	18.29	-405.90	-58.6
0081	18.30	-234.00	-99.3
0082	18.31	127.60	-192.3
0083	18.32	-16.20	89.4
0084	18.32	366.20	-88.4
0085	18.34	167.90	-102
0086	18.36	-113.70	33.9
0087	18.37	-131.80	265.5
0088	18.41	82.70	103.4
0089	18.41	33.20	283
0090	18.43	476.40	298.3
0091	18.43	50.90	15.2
0092	18.44	78.70	84
0093	18.44	-74.50	-437.1
0094	18.45	-192.90	180.5
0095	18.47	112.50	-38.7
0096	18.49	9.20	163.4
0097	18.50	139.50	-33.2
0098	18.51	145.50	254.2
0099	18.53	262.30	107.2
0100	18.53	160.30	-242
0101	18.57	-253.60	-464.6
0102	18.58	-231.30	78.5
0103	18.59	363.20	-486.6
0104	18.60	-99.20	-71.6
0105	18.60	-5.80	23
0106	18.61	224.00	35.7
0107	18.62	-346.00	-140.6
0108	18.66	-43.30	21
0109	18.67	-340.80	65
0110	18.68	52.10	183.8
0111	18.69	-76.10	172.8
0112	18.70	-78.70	-401.6
0113	18.70	-107.70	-124.9
0114	18.71	394.10	52.7
0115	18.73	-224.90	222.5
0116	18.75	-101.10	147.8
0117	18.76	494.40	51
0118	18.77	7.90	38.2
0119	18.79	-103.80	-220.2
0120	18.79	61.10	174.4
0121	18.81	-150.20	189.2
0122	18.81	-197.10	92.3
0123	18.81	-1.80	-53.7
0124	18.83	326.40	-165.2
0125	18.84	-40.80	-95.8
0126	18.84	-299.00	282
0127	18.84	76.20	-282.1
0128	18.85	23.70	-172.5
0129	18.85	75.30	-7.9
0130	18.86	51.10	-20.7
0131	18.86	76.40	-225.7
0132	18.86	-11.30	68
0133	18.87	31.70	76.1
0134	18.89	-150.40	-54.3
0135	18.90	84.60	74.8
0136	18.92	-15.20	28
0137	18.92	-109.20	-137.2
0138	18.93	-462.80	-251.3
0139	18.94	168.10	-78.6
0140	18.94	-15.70	13.7
0141	18.95	-14.10	-369.9
0142	18.95	354.10	176.8
0143	18.96	-159.50	112.9
0144	18.97	51.40	462.2
0145	19.00	220.70	-247.8
0146	19.02	53.40	115.8
0147	19.03	-50.40	-21.6
0148	19.04	-14.60	-155.2
0149	19.05	-345.80	94.4
0150	19.05	442.40	-101.5
0151	19.05	-385.30	436.8
0152	19.07	3.00	-105.9
0153	19.08	-168.50	-432.9
0154	19.09	489.00	-270.6
0155	19.09	482.50	-466.4
0156	19.11	-79.90	-326.7
0157	19.11	-26.70	-6.8
0158	19.12	-7.70	27.5
0159	19.12	3.00	265.7
0160	19.13	-56.20	312.8
0161	19.13	-418.60	-287.7
0162	19.14	-160.00	291.8
0163	19.17	-309.00	-199.4
0164	19.17	-365.10	293
0165	19.19	96.13	517.9
0166	19.19	0.72	165.3
0167	19.21	50.17	-23.4
0168	19.21	-56.60	133.4
0169	19.22	5.65	10.2
0170	19.24	-128.72	181.1
0171	19.27	-274.96	183.7
0172	19.28	-242.64	-29.8
0173	19.29	-125.49	253.7
0174	19.31	-19.44	-32.2
0175	19.31	143.68	-72.6
0176	19.31	-287.43	320.8
0177	19.32	-215.38	-86.8
0178	19.33	-201.81	73.2
0179	19.33	247.77	280.8
0180	19.34	115.36	108
0181	19.34	519.34	-118.3
0182	19.34	-93.05	15.3
0183	19.34	257.99	26.1
0184	19.35	73.27	-5
0185	19.36	265.51	316.8
0186	19.36	-112.15	-41.48
0187	19.37	0.31	14.48
0188	19.41	1.88	71.31
0189	19.42	-58.94	230.09
0190	19.42	305.18	341.27
0191	19.44	-176.96	207.36
0192	19.46	73.71	-104.01
0193	19.46	210.15	-258.65
0194	19.49	-193.54	449.62
0195	19.50	-222.23	372.79
0196	19.50	136.95	-24.06
0197	19.51	-365.97	-394.7
0198	19.52	148.56	484.86
0199	19.52	343.76	133.82
0200	19.55	25.47	137.34
0201	19.55	292.33	-205.85
0202	19.56	310.35	119.48
0203	19.57	-228.92	-145.43
0204	19.57	-45.15	52.48
0205	19.57	-73.61	112.99
0206	19.61	433.58	412.43
0207	19.62	-137.09	167.18
0208	19.62	-11.20	110.35
0209	19.62	-119.38	-332.65
0210	19.62	-149.96	-42.5
0211	19.63	-99.41	300.09
0212	19.63	-393.75	218.9
0213	19.64	501.90	-139.18
0214	19.65	239.82	-455.83
0215	19.67	29.37	-158.87
0216	19.67	347.57	-187.57
0217	19.68	325.62	-281.24
0218	19.70	408.44	154.71
0219	19.71	128.73	-454.49
0220	19.72	44.27	-192.14
0221	19.74	108.35	388.53
0222	19.75	471.84	137.96
0223	19.77	238.07	-225.32
0224	19.77	348.54	-305.5
0225	19.77	-185.02	355.1
0226	19.77	-195.97	114.32
0227	19.77	-146.14	-375.8
0228	19.79	-33.19	-20.78
0229	19.79	313.18	185.63
0230	19.80	-206.38	176
0231	19.80	-4.73	273.44
0232	19.80	-206.38	176
0233	19.80	-387.39	188.19
0234	19.83	-46.57	133.63
0235	19.83	489.83	345.31
0236	19.83	-17.91	-66.16
0237	19.84	-62.12	-132.44
0238	19.84	-17.23	395.2
0239	19.84	-211.46	235.36
0240	19.87	78.20	8.14
0241	19.87	-39.45	36.14
0242	19.88	273.57	-122.82
0243	19.88	443.55	-351.34
0244	19.88	157.75	-214.8
0245	19.90	167.06	-169.47
0246	19.91	-190.50	155.5
0247	19.91	-4.80	297.59
0248	19.91	-32.62	30.62
0249	19.93	154.55	-250.67
0250	19.94	-119.31	335.38
0251	19.94	-152.18	344.21
0252	19.96	-235.99	170.34
0253	19.97	120.08	255.55
0254	19.97	-173.68	-188.52
0255	19.97	-57.89	160.47
0256	19.99	113.83	-75.18
0257	19.99	112.15	-125.92
0258	19.99	169.62	-9.83
0259	20.02	249.92	414.3
0260	20.02	84.90	404.16
0261	20.03	486.28	-270.42
0262	20.03	-95.53	-56.89
0263	20.03	248.34	418.53
0264	20.04	85.04	-203.77
0265	20.04	248.34	418.53
0266	20.04	-1.08	193.02
0267	20.04	125.81	215.09
0268	20.05	480.23	-222.05
0269	20.05	-211.47	149.17
0270	20.05	503.71	305.38
0271	20.06	-304.99	6.2
0272	20.06	467.11	-473.93
0273	20.06	-436.93	257.67
0274	20.09	-13.86	-77.08
0275	20.12	444.87	-78.74
0276	20.12	198.13	-139.23
0277	20.13	-6.93	100.25
0278	20.14	-157.32	173.87
0279	20.15	-460.94	76.86
0280	20.16	266.35	-251.71
0281	20.16	177.97	64.04
0282	20.18	260.74	47.85
0283	20.18	-122.43	412.03
0284	20.19	127.73	148.71
0285	20.19	274.23	22.38
0286	20.21	290.27	-160.98
0287	20.21	-411.99	454.79
0288	20.21	272.64	-433.31
0289	20.22	-149.06	11.75
0290	20.23	-95.89	44.33
0291	20.26	43.55	485.49
0292	20.27	46.31	62.5
0293	20.28	213.90	183.18
0294	20.30	-205.72	-223.85
0295	20.30	245.10	499.73
0296	20.31	80.10	-22.02
0297	20.31	5.63	-50.68
0298	20.32	-4.92	-469.98
0299	20.32	-33.44	-36.3
0300	20.34	-46.99	234.37
0301	20.36	38.69	-178.47
0302	20.37	-177.45	63.55
0303	20.37	125.88	-253.71
0304	20.42	42.94	138.18
0305	20.43	161.27	-109.3
0306	20.46	135.54	513.27
0307	20.48	88.60	80.63
0308	20.49	81.19	220.11
0309	20.50	-390.25	174.25
0310	20.52	-68.68	25.09
0311	20.54	-334.38	213.51
0312	20.55	360.07	397.22
0313	20.57	-434.98	-24.03
0314	20.58	489.16	-368.86
0315	20.58	251.69	-331.42
0316	20.59	524.21	57.54
0317	20.60	-376.65	-152.4
0318	20.60	-315.02	342.3
0319	20.62	-110.52	15.58
0320	20.71	-34.51	22.78
0321	20.72	-136.01	162.44
0322	20.73	-242.80	-433.82
0323	20.73	27.35	67.74
0324	20.74	240.05	-188.98
0325	20.75	-309.32	-374.76
0326	20.76	0.24	62.37
0327	20.76	213.73	122.43
0328	20.77	-76.07	-117.04
0329	20.80	504.29	-138.96
0330	20.81	-59.39	163.59
0331	20.84	51.19	331.02
0332	20.85	263.97	80.71
0333	20.85	318.57	244.36
0334	20.85	465.91	365.39
0335	20.88	99.93	94.15
0336	20.91	125.98	-39.61
0337	20.92	31.86	503.3
0338	20.93	-123.07	348.67
0339	20.94	-213.99	-339.3
0340	20.95	-326.16	190.65
0341	20.96	436.46	403.84
0342	20.96	-333.55	44.9
0343	20.96	78.12	-60.3
0344	20.97	-74.21	-105.45
0345	20.97	-72.26	209.96
0346	20.97	-366.37	521.55
0347	20.98	-236.96	-75.19
0348	20.98	-483.63	374.89
0349	21.00	-257.64	-470.55
0350	21.02	117.77	224.39
0351	21.02	278.72	-167.45
0352	21.05	104.93	-97.55
0353	21.05	-92.99	-59.69
0354	21.06	-451.32	236.08
0355	21.07	-280.95	-9.39
0356	21.07	271.05	-73.26
0357	21.09	-229.10	358.88
0358	21.09	-38.15	-71.17
0359	21.10	124.42	-430.78
0360	21.10	114.19	508.97
0361	21.12	-328.26	144.48
0362	21.12	37.81	56.83
0363	21.14	112.98	-207.49
0364	21.22	44.65	-324.42
0365	21.22	-377.93	-264.95
0366	21.22	-21.80	486.82
0367	21.23	384.57	-372.4
0368	21.23	-66.16	-401.32
0369	21.24	193.36	161.87
0370	21.25	-133.47	-75.15
0371	21.25	-170.11	39.78
0372	21.28	27.74	24.46
0373	21.29	380.90	-395.93
0374	21.30	-111.17	366.99
0375	21.31	-171.53	155.93
0376	21.33	138.77	242.39
0377	21.33	7.70	26.9
0378	21.34	-292.33	488.23
0379	21.38	105.65	-259.44
0380	21.38	-108.19	162.41
0381	21.43	-23.99	11.17
0382	21.45	-202.71	-415.56
0383	21.45	-14.48	487.43
0384	21.47	-412.30	-397.28
0385	21.50	135.18	-303.4
0386	21.51	-186.91	-194.84
0387	21.51	-279.83	220.24
0388	21.52	-149.09	440.58
0389	21.52	-108.40	222.62
0390	21.53	-136.61	29.71
0391	21.54	281.50	-329
0392	21.54	-210.64	106.7
0393	21.55	-412.74	-341.27
0394	21.56	-151.63	28.06
0395	21.56	39.27	421.12
0396	21.57	-163.49	-82.15
0397	21.58	-13.93	41.94
0398	21.59	0.95	487.73
0399	21.59	11.59	106.98
0400	21.62	520.12	-321.96
0401	21.63	526.57	-219.44
0402	21.65	-325.24	-56.54
0403	21.66	-83.79	-179.89
0404	21.66	-51.78	20.1
0405	21.67	-156.23	-33.52
0406	21.69	-112.05	-57.28
0407	21.69	-324.26	178.46
0408	21.72	-92.31	-280.44
0409	21.73	-136.65	246.31
0410	21.78	263.53	-423.7
0411	21.79	-138.18	-3.9
0412	21.81	284.92	408.7
0413	21.81	344.30	-483.84
0414	21.82	71.71	-46.51
0415	21.82	117.65	-75.92
0416	21.86	-214.64	413.18
0417	21.86	-317.54	53.96
0418	21.88	407.48	-40.01
0419	21.89	17.63	-232.06
0420	21.89	0.76	55.45
0421	21.90	-101.48	-415.67
0422	21.95	187.38	-38.81
0423	21.95	-97.22	71.44
0424	21.98	310.78	427.33
0425	21.98	479.88	359.14
0426	21.99	-355.76	145.79
0427	22.09	-447.66	-75.76
0428	22.15	-464.14	455.43
0429	22.16	428.57	-302.44
"""

In [74]:
webda_xy = [l.split() for l in webda_xy_str.split('\n') if l]
webda_xy = [{'webda': int(l[0]), 'V': float(l[1]), 'x': float(l[2]), 'y': float(l[3])} for l in webda_xy]
webda_xy[164]

{'webda': 165, 'V': 19.19, 'x': 96.13, 'y': 517.9}

In [75]:
"""
SDSS 11 is the SDSS coordinates for Webda/Macminn object 0011. In the Webda location char this is considered the center, or (0, 0).
"""
sdss_11 = astropy.coordinates.SkyCoord(ra=cross[3]['ra']*u.degree, dec=cross[3]['dec']*u.degree, frame='icrs')
sdss_11

<SkyCoord (ICRS): (ra, dec) in deg
    (83.15317878, 0.18467629)>

In [76]:
webda_id_col = astropy.table.Column(data=[0] * len(region.cat), name='webda_id', dtype='int64')
webda_V_col = astropy.table.Column(data=[0.0] * len(region.cat), name='webda_V', dtype='float64')
if 'webda_id' in region.cat.colnames:
    del region.cat['webda_id']
if 'webda_V' in region.cat.colnames:
    del region.cat['webda_V']
region.cat.add_column(webda_id_col)
region.cat.add_column(webda_V_col)


In [77]:
region.cat

<Table length=255>
       objID               ra               dec        ... webda_id webda_V
       int64            float64           float64      ...  int64   float64
------------------- ---------------- ----------------- ... -------- -------
1237671557008589197 83.1174678044938 0.191757393983904 ...        0     0.0
1237671557008589440 83.1169430396718 0.158834963274736 ...        0     0.0
1237671557008589319 83.1577623602642 0.161677185756651 ...        0     0.0
1237671557008589072 83.1581215121861 0.186002765163128 ...        0     0.0
1237674284857164078  83.117598869772 0.216236218527777 ...        0     0.0
1237671557008589074 83.1497796851746 0.190780569716583 ...        0     0.0
1237671557008589075 83.1623008522707 0.188989889069686 ...        0     0.0
1237671557008589205 83.1257228647586  0.18421661405784 ...        0     0.0
1237671557008589243 83.1634203097809 0.175285002234588 ...        0     0.0
1237671557008589077 83.1531787784534 0.184676287057929 ...        0     0.0
                ...              ...               ... ...      ...     ...
1237666408478803543 83.1774099999524 0.219176110582921 ...        0     0.0
1237646750359879860 83.1820941133188 0.143597568119076 ...        0     0.0
1237666408478803408 83.1351827953177 0.219733610746305 ...        0     0.0
1237671557008589915 83.1263020612798 0.189384981756461 ...        0     0.0
1237671557008590732 83.1876579580804 0.181144487379884 ...        0     0.0
1237671557008590054 83.1546795176121 0.164938550806364 ...        0     0.0
1237666408478803561 83.1836831858068 0.221563132408232 ...        0     0.0
1237666408478869384 83.2000229873328 0.214346943100592 ...        0     0.0
1237674284857165308 83.1140089903866 0.223418080510584 ...        0     0.0
1237646750359881437 83.1893981271797 0.158973297228933 ...        0     0.0

In [78]:
def match_coord2(coord):
    """Return a list of tuples with the SDSS objID and row for objects close to the coord location."""
    matches = []
    for id_, c in coords:
        match = is_match(coord, c, atol=1.e-4)
        if not match:
            match = is_match(coord, c, atol=1.e-3)
        if match:
            matches.append(id_)
    matches_row = []
    for row in region.cat:
        if row['objID'] in matches:
            matches_row.append(row)
    return matches_row


def match_webda_row(row):
    x, y = row['x'], row['y']
    ra_offset = - x * 8.45e-5 * u.degree # 8.5
    dec_offset = - y * 8.45e-5 * u.degree
    webda_coord = astropy.coordinates.SkyCoord(ra=sdss_11.ra-ra_offset, dec=sdss_11.dec-dec_offset, frame='icrs')
    return match_coord2(webda_coord)


webda_matches = []


for w in webda_xy:
    match_ = match_webda_row(w)
    if match_:
        webda_matches.append((w, match_))

In [79]:
len(webda_matches)

412

In [80]:
webda_matches

[({'webda': 1, 'V': 13.33, 'x': -422.1, 'y': 81.7}, [<Row index=0>
          objID               ra               dec           u        g        r        i       z     psfMag_u psfMag_g psfMag_r psfMag_i psfMag_z psfMagErr_u psfMagErr_g psfMagErr_r psfMagErr_i psfMagErr_z      flags      skyVersion       raErr              decErr       extinction_u extinction_g extinction_r extinction_i extinction_z modelMag_u modelMag_g modelMag_r modelMag_i modelMag_z dered_u  dered_g dered_r  dered_i  dered_z  specObjID   score   webda_id webda_V
          int64            float64           float64      float64  float64  float64  float64 float64  float64  float64  float64  float64  float64    float64     float64     float64     float64     float64        int64        int64         float64            float64         float64      float64      float64      float64      float64     float64    float64    float64    float64    float64   float64  float64 float64  float64  float64    int64    float64   int

In [10]:
def maxrow(row_list):
    max_ = row_list[0]
    for r in row_list:
        # Note astronomers are insane so max is actually min mathematically.
        if r['g'] < max_['g']:
            max_ = r
    return max_

table_rows = []

for _, row_list in webda_matches:
    if row_list and len(row_list) >= 1:
        table_rows.append(maxrow(row_list))

table_rows

t = astropy.table.Table(names=[c for c in table_rows[0].columns], rows=table_rows)
t

<Table length=414>
       objID               ra               dec        ... specObjID   score  
       int64            float64           float64      ...   int64    float64 
------------------- ---------------- ----------------- ... --------- ---------
1237671557008589197 83.1174678044938 0.191757393983904 ...         0 0.8764777
1237671557008589440 83.1169430396718 0.158834963274736 ...         0 0.8764777
1237671557008589319 83.1577623602642 0.161677185756651 ...         0 0.8764777
1237671557008589132 83.1598662951192 0.191763428612551 ...         0 0.8764777
1237671557008589072 83.1581215121861 0.186002765163128 ...         0 0.8764777
1237674284857164078  83.117598869772 0.216236218527777 ...         0 0.9165667
1237671557008589074 83.1497796851746 0.190780569716583 ...         0 0.8764777
1237671557008589075 83.1623008522707 0.188989889069686 ...         0 0.8764777
1237671557008589205 83.1257228647586  0.18421661405784 ...         0 0.8764777
1237671557008589243 83.1634203097809 0.175285002234588 ...         0 0.8764777
                ...              ...               ... ...       ...       ...
1237671557008589075 83.1623008522707 0.188989889069686 ...         0 0.8764777
1237671557008590834 83.1358665166241 0.149584648319021 ...         0 0.8764777
1237671557008589952 83.1649685074201 0.181818210021677 ...         0 0.8764777
1237671557008589074 83.1497796851746 0.190780569716583 ...         0 0.8764777
1237666408478802788 83.1743233414455 0.219997515692015 ...         0 0.8651918
1237666408478802824 83.1927178018791 0.215421443620432 ...         0 0.8651918
1237671557008590677 83.1231168322665 0.197201157122219 ...         0 0.8764777
1237671557008589972 83.1205458549717 0.179002671296141 ...         0 0.8764777
1237674284857164908  83.118487164414 0.223325142514892 ...         0 0.9165667
1237671557008590076 83.1825632233717 0.158695382488756 ...         0 0.8764777

In [81]:
def V_lupton(row):
    return row['g'] - 0.5784 * (row['g'] - row['r']) - 0.0038

def V_close_row(row_list, match_V):
    best, best_V = row_list[0], V_lupton(row_list[0])
    diff_V = abs(best_V - match_V)
    for r in row_list:
        # Note astronomers are insane so max is actually min mathematically.
        V = V_lupton(r)
        if abs(match_V - V) < diff_V:
            best = r
            diff_V = abs(match_V - V)
            best_V = V
    return best

table_rows_V = []

for webda, row_list in webda_matches:
    if row_list and len(row_list) >= 1:
        row  = V_close_row(row_list, webda['V'])
        row['webda_id'] = webda['webda']
        row['webda_V'] = webda['V']
        table_rows_V.append(V_close_row(row_list, webda['V']))

#t = astropy.table.Table(names=[c for c in table_rows_V[0].columns], dtype=['int64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64'], rows=table_rows_V)
#t_dropped = t.to_pandas().drop_duplicates()
#t
#table_rows_V[0].dtype.fields

names = [c for c in table_rows_V[0].columns]
dtypes = [dt.name for dt, _ in table_rows_V[0].dtype.fields.values()]
t = astropy.table.Table(names=names,
                        dtype=dtypes,
                        rows=table_rows_V)
t_dropped = t.to_pandas().drop_duplicates()

In [88]:
names = [c for c in table_rows_V[0].columns]
dtypes = [dt.name for dt, _ in table_rows_V[0].dtype.fields.values()]
t = astropy.table.Table(names=names,
                        dtype=dtypes,
                        rows=table_rows_V)
t_dropped = t.to_pandas().drop_duplicates().reset_index(drop=True)
t_dropped

objID         ra       dec         u         g         r  \
0    1237671557008589197  83.117468  0.191757  13.68412  12.85147  12.70815   
1    1237671557008589440  83.116943  0.158835  14.07516  13.15498  12.95552   
2    1237671557008589319  83.157762  0.161677  15.30769  13.60827  12.83488   
3    1237671557008589132  83.159866  0.191763  19.24988  18.03108  17.76947   
4    1237671557008589072  83.158122  0.186003  17.54163  14.76850  13.78782   
5    1237674284857164078  83.117599  0.216236  15.49111  14.45863  14.15188   
6    1237671557008589074  83.149780  0.190781  16.25564  14.71144  14.21998   
7    1237671557008589075  83.162301  0.188990  17.79490  15.08252  14.17486   
8    1237671557008589205  83.125723  0.184217  16.05728  14.93962  14.57765   
9    1237671557008589243  83.163420  0.175285  17.47545  15.55535  14.87189   
10   1237671557008589077  83.153179  0.184676  18.24195  16.02759  15.28667   
11   1237671557008589294  83.173135  0.167409  17.67119  15.80577  15.12104   
12   1237666408478802174  83.145959  0.209804  16.66850  15.65669  15.58583   
13   1237671557008589085  83.158854  0.188077  19.01326  16.88556  16.27375   
14   1237674284857164097  83.129118  0.227452  17.10259  16.03694  15.71305   
15   1237671557008589100  83.149288  0.188826  23.60608  17.12125  17.02260   
16   1237671557008589175  83.123687  0.207246  17.07599  16.11291  15.82443   
17   1237671557008589099  83.143403  0.177829  18.04652  16.89201  16.96056   
18   1237671557008589101  83.156936  0.186504  18.63495  17.52965  17.21815   
19   1237671557008589090  83.145989  0.182621  18.91783  17.10843  16.54424   
20   1237671557008589079  83.153650  0.197085  18.56215  16.68306  16.01934   
21   1237671557008589321  83.162468  0.157569  17.47698  16.50696  16.23041   
22   1237671557008589430  83.119281  0.160026  19.17227  16.92732  16.11890   
23   1237671557008590068  83.138346  0.159634  18.61893  16.88370  16.17904   
24   1237671557008589112  83.155159  0.188506  19.10708  17.75135  17.41157   
25   1237671557008589083  83.176345  0.208188  17.42787  16.39313  16.06607   
26   1237671557008589122  83.143565  0.187595  18.95115  17.92877  17.68797   
27   1237671557008589121  83.153075  0.183582  18.88331  17.76983  17.48325   
28   1237671557008589091  83.138594  0.181457  19.02947  17.29071  16.62191   
29   1237671557008589092  83.154179  0.200160  18.87375  17.17545  16.55717   
..                   ...        ...       ...       ...       ...       ...   
225  1237666408478803472  83.153436  0.225970  22.74550  21.28755  20.72883   
226  1237671557008590828  83.185619  0.152959  22.87289  21.32794  19.92123   
227  1237671557008590107  83.147454  0.150728  21.60387  20.94665  20.57774   
228  1237671557008590324  83.185146  0.150991  20.75844  20.69488  20.70129   
229  1237666408478802168  83.143576  0.215185  23.51432  23.31262  22.02139   
230  1237671557008589148  83.157511  0.185975  23.61906  24.36724  24.26030   
231  1237674284857164099  83.128584  0.226105  22.47021  21.18718  20.41616   
232  1237671557008590796  83.168635  0.163120  23.55936  22.51829  21.81396   
233  1237671557008590834  83.135867  0.149585  22.65070  21.11162  20.67317   
234  1237666408478803473  83.152718  0.225336  24.65513  22.18568  21.10557   
235  1237671557008590036  83.137318  0.168288  23.26408  21.33995  20.72501   
236  1237671557008589852  83.136289  0.203900  22.41377  23.86278  22.52613   
237  1237671557008590686  83.133371  0.194137  22.60233  22.06199  21.04199   
238  1237671557008589433  83.118092  0.155925  22.89325  21.76314  20.90760   
239  1237666408478803486  83.158779  0.220306  24.39537  22.26369  21.64524   
240  1237646750359881103  83.197071  0.157233  24.06877  21.93222  20.59551   
241  1237671557008589972  83.120546  0.179003  24.17086  22.27535  21.26252   
242  1237671557008590772  83.146010  0.169499  23.73940  21.80131  20.55047   
243  1237671557008590807  83.149405  0.161435  23.57699  22.17880  21

In [ ]:
row = table_rows_V[0]
dtype = row.dtype
dts = [dt.name for dt, _ in dtype.fields.values()]
dt = dts[0]
dt.name

In [ ]:
shrd = aww.visual.SHRD(horizontal=False)
shrd.cat = t
shrd.show() # 1 17 2 17 1

In [ ]:
shrd.aladin.selection_ids = [str(r['objID']) for r in t]

In [ ]:
[t[1][1] for t in t_dropped.iteritems()]

In [ ]:
# webda_6 = webda_matches[5]
dt = webda_6[1][0].dtype
dt.fields.values()
['int64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64']

In [ ]:
webda_6

In [ ]:
macminn_count = len(macminn_dat)
webda_match_count = len(webda_matches)
match_percentage = (macminn_count -(macminn_count - webda_match_count))/macminn_count
match_percentage

In [89]:
VERSION = 5
#df_sdss_macminn = t_dropped.to_pandas()
t_dropped.to_pickle('sdss_macminn.dataframe.v{0}.bz2.pickle'.format(VERSION))

In [90]:
# Use read_pickle to load the pickled DataFrame.
sdss_macminn_loaded = pd.read_pickle('sdss_macminn.dataframe.v5.bz2.pickle')
sdss_macminn_loaded

objID         ra       dec         u         g         r  \
0    1237671557008589197  83.117468  0.191757  13.68412  12.85147  12.70815   
1    1237671557008589440  83.116943  0.158835  14.07516  13.15498  12.95552   
2    1237671557008589319  83.157762  0.161677  15.30769  13.60827  12.83488   
3    1237671557008589132  83.159866  0.191763  19.24988  18.03108  17.76947   
4    1237671557008589072  83.158122  0.186003  17.54163  14.76850  13.78782   
5    1237674284857164078  83.117599  0.216236  15.49111  14.45863  14.15188   
6    1237671557008589074  83.149780  0.190781  16.25564  14.71144  14.21998   
7    1237671557008589075  83.162301  0.188990  17.79490  15.08252  14.17486   
8    1237671557008589205  83.125723  0.184217  16.05728  14.93962  14.57765   
9    1237671557008589243  83.163420  0.175285  17.47545  15.55535  14.87189   
10   1237671557008589077  83.153179  0.184676  18.24195  16.02759  15.28667   
11   1237671557008589294  83.173135  0.167409  17.67119  15.80577  15.12104   
12   1237666408478802174  83.145959  0.209804  16.66850  15.65669  15.58583   
13   1237671557008589085  83.158854  0.188077  19.01326  16.88556  16.27375   
14   1237674284857164097  83.129118  0.227452  17.10259  16.03694  15.71305   
15   1237671557008589100  83.149288  0.188826  23.60608  17.12125  17.02260   
16   1237671557008589175  83.123687  0.207246  17.07599  16.11291  15.82443   
17   1237671557008589099  83.143403  0.177829  18.04652  16.89201  16.96056   
18   1237671557008589101  83.156936  0.186504  18.63495  17.52965  17.21815   
19   1237671557008589090  83.145989  0.182621  18.91783  17.10843  16.54424   
20   1237671557008589079  83.153650  0.197085  18.56215  16.68306  16.01934   
21   1237671557008589321  83.162468  0.157569  17.47698  16.50696  16.23041   
22   1237671557008589430  83.119281  0.160026  19.17227  16.92732  16.11890   
23   1237671557008590068  83.138346  0.159634  18.61893  16.88370  16.17904   
24   1237671557008589112  83.155159  0.188506  19.10708  17.75135  17.41157   
25   1237671557008589083  83.176345  0.208188  17.42787  16.39313  16.06607   
26   1237671557008589122  83.143565  0.187595  18.95115  17.92877  17.68797   
27   1237671557008589121  83.153075  0.183582  18.88331  17.76983  17.48325   
28   1237671557008589091  83.138594  0.181457  19.02947  17.29071  16.62191   
29   1237671557008589092  83.154179  0.200160  18.87375  17.17545  16.55717   
..                   ...        ...       ...       ...       ...       ...   
225  1237666408478803472  83.153436  0.225970  22.74550  21.28755  20.72883   
226  1237671557008590828  83.185619  0.152959  22.87289  21.32794  19.92123   
227  1237671557008590107  83.147454  0.150728  21.60387  20.94665  20.57774   
228  1237671557008590324  83.185146  0.150991  20.75844  20.69488  20.70129   
229  1237666408478802168  83.143576  0.215185  23.51432  23.31262  22.02139   
230  1237671557008589148  83.157511  0.185975  23.61906  24.36724  24.26030   
231  1237674284857164099  83.128584  0.226105  22.47021  21.18718  20.41616   
232  1237671557008590796  83.168635  0.163120  23.55936  22.51829  21.81396   
233  1237671557008590834  83.135867  0.149585  22.65070  21.11162  20.67317   
234  1237666408478803473  83.152718  0.225336  24.65513  22.18568  21.10557   
235  1237671557008590036  83.137318  0.168288  23.26408  21.33995  20.72501   
236  1237671557008589852  83.136289  0.203900  22.41377  23.86278  22.52613   
237  1237671557008590686  83.133371  0.194137  22.60233  22.06199  21.04199   
238  1237671557008589433  83.118092  0.155925  22.89325  21.76314  20.90760   
239  1237666408478803486  83.158779  0.220306  24.39537  22.26369  21.64524   
240  1237646750359881103  83.197071  0.157233  24.06877  21.93222  20.59551   
241  1237671557008589972  83.120546  0.179003  24.17086  22.27535  21.26252   
242  1237671557008590772  83.146010  0.169499  23.73940  21.80131  20.55047   
243  1237671557008590807  83.149405  0.161435  23.57699  22.17880  21

In [ ]:
load_match = []
for idx, sdss_row in sdss_macminn_loaded.iterrows():
    if np.isclose(sdss_row['ra'], 83.149780):
        load_match.append((idx,sdss_row))
load_match

In [ ]:
SDSSRegion(astropy.table.Table.from_pandas(sdss_macminn_loaded))

In [66]:
region.cat.

<Table length=255>
       objID               ra               dec        ... webda_id webda_V
       int64            float64           float64      ...  int64   float64
------------------- ---------------- ----------------- ... -------- -------
1237671557008589197 83.1174678044938 0.191757393983904 ...        1   13.33
1237671557008589440 83.1169430396718 0.158834963274736 ...        2    13.6
1237671557008589319 83.1577623602642 0.161677185756651 ...        3   13.68
1237671557008589072 83.1581215121861 0.186002765163128 ...        5   21.43
1237674284857164078  83.117598869772 0.216236218527777 ...        6   14.93
1237671557008589074 83.1497796851746 0.190780569716583 ...        7   21.95
1237671557008589075 83.1623008522707 0.188989889069686 ...        8   21.89
1237671557008589205 83.1257228647586  0.18421661405784 ...        9   15.32
1237671557008589243 83.1634203097809 0.175285002234588 ...       10   20.43
1237671557008589077 83.1531787784534 0.184676287057929 ...       11   19.35
                ...              ...               ... ...      ...     ...
1237666408478803543 83.1774099999524 0.219176110582921 ...      263   20.03
1237646750359879860 83.1820941133188 0.143597568119076 ...      413   21.81
1237666408478803408 83.1351827953177 0.219733610746305 ...      416   21.86
1237671557008589915 83.1263020612798 0.189384981756461 ...      417   21.86
1237671557008590732 83.1876579580804 0.181144487379884 ...      418   21.88
1237671557008590054 83.1546795176121 0.164938550806364 ...      419   21.89
1237666408478803561 83.1836831858068 0.221563132408232 ...      424   21.98
1237666408478869384 83.2000229873328 0.214346943100592 ...      425   21.98
1237674284857165308 83.1140089903866 0.223418080510584 ...      428   22.15
1237646750359881437 83.1893981271797 0.158973297228933 ...      429   22.16

In [69]:
VERSION = 4
region.cat.to_pandas().to_pickle('sdss_macminn.dataframe.v{0}.bz2.pickle'.format(VERSION))

In [70]:
VERSION

4